In [37]:
#default_exp read
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [38]:
import sys
from fastcore.xtras import Path

# Insert in Path Project Directory
sys.path.insert(0, str(Path().cwd().parent))

# Reading
> Este módulo concentra funções para a leitura dos diversos arquivos que compões a base de dados

* `STEL` - Serviços Privados de Telecomunicações
* `RADCOM` - Serviço de Radiodifusão Comunitária
* `MOSAICO` - Demais serviços de Radiodifusão, e.g. TV, RTV, FM, AM, etc.

In [39]:
#export
from typing import Union, Tuple
from pathlib import Path

import pandas as pd
from pyarrow import ArrowInvalid


from anateldb.query import update_mosaico, update_stel, update_radcom, update_base
from anateldb.merge import aero_common, aero_new

## MOSAICO
> O mosaico atualmente é composto por 3 bases complementares originárias de um banco `MongoDB`: `Estações, Plano Básico e Histórico`. Os módulos aqui leem, processam e mesclam as duas primeiras.

In [40]:
#export
def read_df(folder: Union[str, Path], stem: str) -> pd.DataFrame:
    """Lê o dataframe formado por folder / stem.[parquet.gzip | fth | xslx]"""
    file = Path(f"{folder}/{stem}.parquet.gzip")
    try:
        df = pd.read_parquet(file)
    except (ArrowInvalid, FileNotFoundError):
        file = Path(f"{folder}/{stem}.fth")
        try:
            df = pd.read_feather(file)
        except (ArrowInvalid, FileNotFoundError):
            file = Path(f"{folder}/{stem}.xlsx")
            try:
                df = pd.read_excel(file, engine="openpyxl", sheet_name="DataBase")
            except Exception as e:
                raise ValueError(f"Error when reading {file}") from e
    return df


def read_mosaico(folder: Union[str, Path], update: bool = False) -> pd.DataFrame:
    """Lê o banco de dados salvo localmente do MOSAICO e opcionalmente o atualiza."""
    return update_mosaico(folder) if update else read_df(folder, "mosaico")

In [43]:
folder = Path.cwd().parent / 'dados'

In [44]:
mosaico = read_mosaico(folder)
mosaico

Num_Serviço             Id Número_Estação   Latitude  Longitude  \
0             248  57dbaad053c60           <NA>  -7.614167 -72.895833   
1             248  57dbaad0dc4e3      322647029 -12.101389 -44.993611   
2             248  57dbaad0eb54a      322623553 -14.779444 -39.262222   
3             248  57dbaad0ef8af      322623537 -14.781670 -39.261670   
4             248  57dbaad1077a6      637062230 -16.353056 -39.386111   
...           ...            ...            ...        ...        ...   
29651         801  62b0adc1c8c91           <NA> -27.506600 -49.287000   
29652         801  62b0b38c7d2b9           <NA> -27.506600 -49.287000   
29653         205  57dbac6b65c67      322480280 -25.492550 -49.153450   
29654         801  62c8629921605           <NA> -16.767600 -47.613100   
29655         230  5fae8fad66ac6      323269206  -9.160330 -36.032830   

      Validade_RF           Município  Frequência Classe Serviço  \
0             NaN         Mâncio Lima      539.00      C      TV   
1      2023-12-31           Barreiras       79.00      A      TV   
2      2023-12-31             Itabuna       69.00      A      TV   
3      2023-12-31             Itabuna      177.00      B      TV   
4      2017-08-20        Porto Seguro      515.00      C      TV   
...           ...                 ...         ...    ...     ...   
29651         NaN       Leoberto Leal      557.00      C    RTVD   
29652         NaN       Leoberto Leal      599.00      C    RTVD   
29653  2024-05-01            Curitiba        0.67      B      OM   
29654         NaN          Cristalina      563.00      C    RTVD   
29655  2018-09-19  União dos Palmares       99.90      C      FM   

                                    Entidade  UF Status            CNPJ  \
0                          X-MEDIAGROUP S.A.  AC  TV-C1  03211814000163   
1                TELEVISAO OESTE BAIANO LTDA  BA  TV-C4  16395923000120   
2                  TELEVISAO SANTA CRUZ LTDA  BA  TV-C2  13476833000175   
3                           TV CABRALIA LTDA  BA  TV-C4  13494265000135   
4                          FUNDACAO FUNDESUL  BA  TV-C7  04188244000109   
...                                      ...  ..    ...             ...   
29651  PREFEITURA MUNICIPAL DE LEOBERTO LEAL  SC  TV-C1  82924390000150   
29652  PREFEITURA MUNICIPAL DE LEOBERTO LEAL  SC  TV-C1  82924390000150   
29653                   RADIO RIO VERDE LTDA  PR  AM-C4  05349869000160   
29654     RF TECNOLOGIA E PARTICIPACOES LTDA  GO  TV-C1  07678601000105   
29655                       RADIO FM AG LTDA  AL  FM-C4  12834222000199   

            Fistel  Coordenadas_do_Município  
0      50410887137                     False  
1      06030116240                     False  
2      06020355110                     False  
3      06020354903                     False  
4      50011828080                     False  
...            ...                       ...  
29651  50442349742                     False  
29652  50442350597                     False  
29653  05008005375                     False  
29654  50442597649                     False  
29655  22000003168                     False  

[29656 rows x 16 columns]

In [46]:
mosaico.to_parquet(f"{folder}/mosaico.parquet.gzip", compression="gzip", index=False)

In [45]:
mosaico.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 29656 entries, 0 to 29655
Data columns (total 16 columns):
 #   Column                    Non-Null Count  Dtype   
---  ------                    --------------  -----   
 0   Num_Serviço               29656 non-null  category
 1   Id                        29656 non-null  string  
 2   Número_Estação            23715 non-null  string  
 3   Latitude                  29656 non-null  float64 
 4   Longitude                 29656 non-null  float64 
 5   Validade_RF               26799 non-null  category
 6   Município                 29653 non-null  category
 7   Frequência                29656 non-null  float64 
 8   Classe                    29640 non-null  category
 9   Serviço                   29656 non-null  category
 10  Entidade                  29637 non-null  category
 11  UF                        29654 non-null  category
 12  Status                    29656 non-null  category
 13  CNPJ                      29656 non-null  cate

In [17]:
mosaico['Frequência'] = mosaico['Frequência'].astype('category')

In [18]:
from pandas_profiling import ProfileReport
mosaico_profile = ProfileReport(mosaico, config_file='report_config.yaml')
mosaico_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## STEL & RADCOM

In [47]:
#export
def read_stel(folder: Union[str, Path], update: bool = False) -> pd.DataFrame:
    """Lê o banco de dados salvo localmente do STEL. Opcionalmente o atualiza pelo Banco de Dados ANATELBDRO01 caso `update = True` ou não exista o arquivo local"""
    return update_stel(folder) if update else read_df(folder, "stel")


def read_radcom(folder: Union[str, Path], update: bool = False) -> pd.DataFrame:
    """Lê o banco de dados salvo localmente de RADCOM. Opcionalmente o atualiza pelo Banco de Dados ANATELBDRO01 caso `update = True` ou não exista o arquivo local"""
    return update_radcom(folder) if update else read_df(folder, "radcom")

In [48]:
radcom = read_radcom(folder)
radcom.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4923 entries, 0 to 4922
Data columns (total 10 columns):
 #   Column          Non-Null Count  Dtype   
---  ------          --------------  -----   
 0   Frequência      4923 non-null   float64 
 1   Entidade        4923 non-null   string  
 2   Fistel          4923 non-null   string  
 3   Número_Estação  4923 non-null   string  
 4   Município       4923 non-null   string  
 5   UF              4923 non-null   category
 6   Latitude        4923 non-null   float64 
 7   Longitude       4923 non-null   float64 
 8   CNPJ            4923 non-null   string  
 9   Classe          4923 non-null   category
dtypes: category(2), float64(3), string(5)
memory usage: 319.4 KB


In [50]:
radcom['Frequência'] = radcom['Frequência'].astype('category')

In [51]:
radcom_profile = ProfileReport(radcom, config_file='report_config.yaml')
radcom_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [52]:
stel = read_stel(folder)
stel.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 880091 entries, 0 to 880090
Data columns (total 14 columns):
 #   Column           Non-Null Count   Dtype   
---  ------           --------------   -----   
 0   Frequência       880091 non-null  float64 
 1   Classe_Emissão   856695 non-null  category
 2   Largura_Emissão  856695 non-null  category
 3   Classe           856697 non-null  category
 4   Num_Serviço      880091 non-null  category
 5   Entidade         880091 non-null  category
 6   Fistel           880091 non-null  category
 7   Número_Estação   880091 non-null  category
 8   Município        879297 non-null  category
 9   UF               879297 non-null  category
 10  Latitude         879297 non-null  float64 
 11  Longitude        879297 non-null  float64 
 12  CNPJ             880091 non-null  category
 13  Validade_RF      880091 non-null  category
dtypes: category(11), float64(3)
memory usage: 44.7 MB


In [54]:
stel['Frequência'] = stel['Frequência'].astype('category')

In [55]:
stel_profile = ProfileReport(stel, config_file='report_config.yaml')
stel_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Bases Externas da Aeronáutica

In [26]:
#export
def read_icao(folder: Union[str, Path], update: bool = False) -> pd.DataFrame:
    """Lê a base de dados do Frequency Finder e Canalização VOR/ILS/DME"""
    if update:
        # TODO: atualizar a base de dados do Frequency Finder e Canalização VOR/ILS/DME
        # update_icao(folder)
        raise NotImplementedError(
            "Atualizar da base de dados do Frequency Finder e Canalização VOR/ILS/DME não implementado"
        )
    return read_df(folder, "icao")


def read_aisw(folder: Union[str, Path], update: bool = False) -> pd.DataFrame:
    """Fontes da informação: AISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME."""
    if update:
        # TODO: Atualizar a base de dados do AISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME
        # update_pmec(folder)
        raise NotImplementedError(
            "Atualizar da base de dados do Frequency Finder e Canalização VOR/ILS/DME não implementado"
        )
    return read_df(folder, "aisw")


def read_aisg(folder: Union[str, Path], update: bool = False) -> pd.DataFrame:
    """Fontes da informação: AISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME."""
    if update:
        # TODO: Atualizar a base de dados do GEOAISWEB
        # update_geo(folder)
        raise NotImplementedError(
            "Atualizar da base de dados do Frequency Finder e Canalização VOR/ILS/DME não implementado"
        )
    return read_df(folder, "aisg")


def read_aero(
    folder: Union[str, Path],
    up_icao: bool = False,
    up_aisw: bool = False,
    up_aisg: bool = False,
) -> Tuple[pd.DataFrame, pd.DataFrame]:
    """Lê os arquivos de dados da aeronáutico e retorna os registros comuns e únicos"""
    icao = read_icao(folder, up_icao)
    pmec = read_aisw(folder, up_aisw)
    geo = read_aisg(folder, up_aisg)
    icao["Description"] = icao.Description.astype("string")
    pmec["Description"] = pmec.Description.astype("string")
    geo["Description"] = geo.Description.astype("string")
    common = aero_common(icao, pmec, geo)
    new = aero_new(icao, pmec, geo)
    return common, new

In [27]:
icao = read_icao(folder)
icao['Frequency'] = icao['Frequency'].astype('category')
icao_profile = ProfileReport(icao, config_file='report_config.yaml')
icao_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [28]:
aisw = read_aisw(folder)
aisw['Frequency'] = aisw['Frequency'].astype('category')
aisw_profile = ProfileReport(aisw, config_file='report_config.yaml')
aisw_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [29]:
aisg = read_aisg(folder)
aisg['Frequency'] = aisg['Frequency'].astype('category')
aisg_profile = ProfileReport(aisg, config_file='report_config.yaml')
aisg_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Base Consolidada

In [30]:
#export
def read_base(folder: Union[str, Path], update: bool = False) -> pd.DataFrame:
    """Lê a base de dados e opcionalmente a atualiza antes da leitura"""
    return update_base(folder) if update else read_df(folder, "base")

In [31]:
base = read_base(folder)
base['Frequência'] = base['Frequência'].astype('category')
base_profile = ProfileReport(base, config_file='report_config.yaml')
base_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [61]:
radcom

Frequência                                           Entidade  \
0          87.5  ASSOCIACAO COMUNITARIA VOZ DA LIBERDADE DE TUR...   
1          87.5  ASSOCIACAO COMUNITARIA DO MORAD.DE ALVORADA DE...   
2          87.5  ASSOCIAÇÃO COMUNITARIA DA JUVENTUDE DE CONGONH...   
3          87.5                     ASSOCIACAO COMUNITARIA FOLHETA   
4          87.5  ASSOCIAÇÃO DE RÁDIO COMUNITÁRIA DE CASTANHEIRA...   
...         ...                                                ...   
4918      107.9  ASSOCIAÇÃO DE MORADORES DO JARDIM CRISTINA OUR...   
4919      107.9  ASSOCIAÇÃO DE MORADORES DO JARDIM CRISTINA OUR...   
4920      107.9  ASSOCIAÇÃO DE MORADORES DO JARDIM CRISTINA OUR...   
4921      107.9  ASSOCIACAO COMUNITARIA CULTURAL DE MUSICA E CI...   
4922      107.9                    ASSOCIAÇÃO CULT COMUNIT MORUMBI   

           Fistel Número_Estação            Município  UF   Latitude  \
0     50415095220     1008210959           Turilândia  MA  -2.228611   
1     50409064718      699491851    Alvorada de Minas  MG -18.734167   
2     50405625782      699359830   Congonhas do Norte  MG -18.812778   
3     50404381251      690859562          Dom Joaquim  MG -18.950000   
4     50411566547     1008401606          Castanheira  MT -11.137222   
...           ...            ...                  ...  ..        ...   
4918  50434484237      692270272  São José dos Campos  SP -23.553056   
4919  50406232911      692270272  São José dos Campos  SP -23.553056   
4920  50413097013      692270272  São José dos Campos  SP -23.553056   
4921  50406778205      693049723  São José dos Campos  SP -23.191944   
4922  50407431578      697707695  São José dos Campos  SP -23.267778   

      Longitude            CNPJ Classe       Status  
0    -45.306667  10910844000123      P    RADCOM, P  
1    -43.364722  00635021000183      3    RADCOM, 3  
2    -43.673611  04868495000126      3    RADCOM, 3  
3    -43.266667  01809521000157      3    RADCOM, 3  
4    -58.613333  14970791000197      P    RADCOM, P  
...         ...             ...    ...          ...  
4918 -45.870556  07249175000186      3    RADCOM, 3  
4919 -45.870556  07249175000186      3    RADCOM, 3  
4920 -45.870556  07249175000186      3    RADCOM, 3  
4921 -45.875278  08894854000170      3    RADCOM, 3  
4922 -45.897500  02521194000104    3-B  RADCOM, 3-B  

[4923 rows x 11 columns]